In [1]:
import sympy
sympy.init_printing()

We attempt to model motion as a series of piecewise-constant jerk segments (where jerk is $d^4p \over dp^4$)

For an individual segment, we have:

In [27]:
sympy.var("p,v,a,j,t,v0,a0, a_max, v_max, j_max, t_a, t_v, t_j", real=True, positive=True)
sympy.Symbol

sympy.core.symbol.Symbol

In [3]:
def seg_d(j=j, a0=a0, v0=v0, t=t, p0=0, following=None):
    if following is not None:
        a0 = following["ae"]
        v0 = following["ve"]
        p0 = following["pe"]
    res = dict(
        dt = t,
        da = t * j,
        dv = j * t**2 / 2 + a0*t,
        dp = j*t**3/6 + a0 * t**2 / 2 + v0 * t
    )
    res["ae"] = res["da"] + a0
    res["ve"] = res["dv"] + v0
    res["pe"] = p0 + res["dp"]
    return dict((k, v.simplify()) for k,v in res.items())
seg_p = seg_d()["dp"]

In [4]:
sympy.Eq(p, seg_p)

      ⎛            2       ⎞
    t⋅⎝3⋅a₀⋅t + j⋅t  + 6⋅v₀⎠
p = ────────────────────────
               6            

We have three machine limits to consider at this point: we have a maximum jerk (derived from the shock limits of the system), maximum acceleration (derived from the torque limits of the servos), and maximum velocity (from the frequency at which we update the steppers). We can ignore the position bounds at this point; the commands to this stage of the motion planner are simply "move by ΔX,ΔY", and so we can assume that the source of those commands will never ask us to move outside the range of motion.

This leaves us with the following general motion profile for a single linear move:
1. $j>0$; Increase acceleration to $a_{max}$
2. $j=0$; continue accelerating at $a_{max}$ to somewhat before $v_{max}$
3. $j<0$; reduce acceleration to 0 to reach constant velocity $v_{max}$
4. $j=0$; proceed at constant velocity to decelleration point
5. $j<0$; begin decelleration to $-a_{max}$
6. $j=0$; decelerate at max rate to just before 0 velocity
7. $j>0$; decrease decelleration until $v=0$

Let's call the time taken for segment $n$ "$t_n$". Note that, through a simple coordinate transform, $t_1=t_3=t_5=t_7$. Further, $t_2=t_6$. We'll rename these to $t_j$ and $t_a$ (for constant jerk and constant accelleration), respectively, and introduce $t_v = t_4$ for consistency.


There are several possible degenerate cases:

* The move is too short to reach $v_{max}$. In this case, we lower $v_max$ accordingly and set $t_v=0$.
* $a_{max}$ is unreachable given the maximum velocity. This results in $t_a$ both being 0 for all moves and the calculation proceeding with lowered $a_{max}$

Note that the first situation can give rise to the second.

We can handle these degenerate situations using the following algorithm:

1. Assume the most general form of the profile. In this case, all but stage 4 is constant-time, so solve for $t_v$
2. If the calculated $t_v < 0$, calculate the actual $v_{max}$ and recalculate $t_a$ holding $t_j$ constant and $t_v=0$.
3. If $t_a<0$, recalculate $t_j$ holding $t_v=t_a=0$

This means that to solve the motion equations, we need a couple of closed-form solutions:

In [5]:
# Time and position calculations for general form
t_j_max = a_max / j_max
p1s1 = seg_d(j=j_max, a0=0, v0=0, t=t_j)
# p1s1

In [6]:
p1s2 = seg_d(j = 0, t = t_a, following=p1s1)
# p1s2

In [7]:
p1s3 = seg_d(j=-j_max, t=t_j, following=p1s2)
# p1s3

In [8]:
t_a_max = sympy.solve(p1s3["ve"].subs(t_j, t_j_max) - v_max, t_a)[0]

In [9]:
p1s3["pe"]

         ⎛  2                   2⎞
jₘₐₓ⋅t_j⋅⎝tₐ  + 3⋅tₐ⋅t_j + 2⋅t_j ⎠
──────────────────────────────────
                2                 

In [10]:
p1s4 = seg_d(j=0, t=t_v, following=p1s3)

In [11]:
p1s5 = seg_d(j=-j_max, t=t_j, following=p1s4)
p1s6 = seg_d(j=0, t=t_a, following=p1s5)
p1s7 = seg_d(j=j_max, t=t_j, following=p1s6)

In [24]:
p1s4['pe']

         ⎛  2                   2                  ⎞
jₘₐₓ⋅t_j⋅⎝tₐ  + 3⋅tₐ⋅t_j + 2⋅t_j  + 2⋅tᵥ⋅(tₐ + t_j)⎠
────────────────────────────────────────────────────
                         2                          

In [13]:
(p1s3["pe"] - sum(x["dp"] for x in [p1s5, p1s6, p1s7])).subs({t_j: t_j_max, t_a: t_a_max}).simplify()

0

In [14]:
p1s7["pe"].subs({t_j: t_j_max, t_a: t_a_max}).simplify()

                          2
aₘₐₓ⋅vₘₐₓ             vₘₐₓ 
───────── + tᵥ⋅vₘₐₓ + ─────
   jₘₐₓ                aₘₐₓ

In [15]:
p1 = p1s7["pe"].subs({t_j: t_j_max, t_a: t_a_max}).simplify()
p2 = p1s7["pe"].subs({t_j: t_j_max, t_v: 0}).simplify()
p3 = p1s7["pe"].subs({t_a: 0, t_v: 0}).simplify()

In [36]:
t_a_max

  aₘₐₓ   vₘₐₓ
- ──── + ────
  jₘₐₓ   aₘₐₓ

In [16]:
p1tv = sympy.solve(p - p1, t_v)[0]
sympy.Eq(t_v, p1tv)

       aₘₐₓ    p     vₘₐₓ
tᵥ = - ──── + ──── - ────
       jₘₐₓ   vₘₐₓ   aₘₐₓ

In [38]:
p2ta = sympy.solve(p - p2, t_a, positive=True)[0].simplify()
sympy.Eq(t_a, p2ta)

                      ___________________
             3/2     ╱     3         2   
     - 3⋅aₘₐₓ    + ╲╱  aₘₐₓ  + 4⋅jₘₐₓ ⋅p 
tₐ = ────────────────────────────────────
                   ______                
               2⋅╲╱ aₘₐₓ ⋅jₘₐₓ           

In [55]:
(p2ta + 3*(a_max ** sympy.Rational(3,2)) / (2 * a_max ** sympy.Rational(1,2) * j_max)).simplify() ** 2

    3         2  
aₘₐₓ  + 4⋅jₘₐₓ ⋅p
─────────────────
              2  
   4⋅aₘₐₓ⋅jₘₐₓ   

In [35]:
p3tj = sympy.solve(p - p3, t_j)[0]
sympy.Eq(t_j, (p3tj**3))

        p   
t_j = ──────
      2⋅jₘₐₓ

# Timing calculations

Now that we have closed-form solutions for each of the timing regimes, we need to know when those formulas apply.

We do this by evaluating $p_{max}$ at each of the transition points:

In [19]:
[ p1s7["pe"].subs(param).simplify() for param in [{t_v: 0, t_a: 0, t_j: t_j_max}, {t_v: 0, t_a: t_a_max, t_j: t_j_max}]]

⎡      3                  2⎤
⎢2⋅aₘₐₓ   aₘₐₓ⋅vₘₐₓ   vₘₐₓ ⎥
⎢───────, ───────── + ─────⎥
⎢     2      jₘₐₓ      aₘₐₓ⎥
⎣ jₘₐₓ                     ⎦

The first of these is where we transition from adjusting $t_j$ to $t_a$, and the second is where we start manipulating $t_v$.

# Control loop simulation

All of these assume that the control loop runs with infinite precision, which is patently false. Rather, for stability, we want to use fixed-point arithmetic as much as possible, using steps/ticks as our units.

To evaluate our results, we implement a simple motion planner and stepper driver simulation, assuming that the driven stage is purely cartesian. When we move to the CoreXY simulation, we will need to perform the coordinate system rotation before motion planning to make this much easier to manage. Alternatively, we could measure position in *half*-steps and decide which side to vibrate on, but TBH, working in motor coordinates seems easier.

In [20]:
class StepperSimulator:
    def __init__(self):
        self.data = []
        self.pos = 0
        self.t = 0
        self.last_step = False
    def tick(self, step, dir):
        self.t += 1
        if step and not self.last_step:
            self.pos += 1 if dir else -1
            self.data.push((self.t, self.pos))
        self.last_step = step

class MotionPlanner:
    MP_FRAC = 8 # 8 fractional bits
    MP_TICK_PER_SEC = 5000
    MP_MM_PER_STEP = 0.000
    MP_AMAX = 0
        

# Implementation notes

## Units
If we choose our units judiciously, all calculations can be integers, removing the need for FP computations in the critical loop and thus removing floating-point inaccuracy from consideration. But which units shall we use?

Obviously, we want to only have to evaluate our motion equations at integral points in time. This suggests the use of the "cycle" as our time unit. This leaves the distance unit to be determined.

At first blush, it seems to make sense to use the motor step size as a distance unit. However, that is only really convenient for measuring *output*; most of the time the control loop will manage fractional steps. So, we need to find something different. Looked at from this angle, we look again at our motion equation:

$$P = \iiint j\,dt = \frac{1}{6}jt^3 + \frac{1}{2}a_0t^2 + v_0t + p_0$$
$$a = jt + a_0$$
$$v = \frac{1}{2}jt^2 + a_0 t+ v_0$$

A small bit of thought is sufficient to show that, assuming that $t$ is always integral, $a$ is always an integral multiple of $j$; $v$ is an integral multiple of $\frac{j}{2}$, and $p$ is always an integral multiple of $\frac{j}{6}$

Thus, our fundamental distance unit is that such that $j_{max} = 6$

Given a $j_{max}$ in $\frac{mm}{s^3}$, a step size of $S$ mm, and a step frequency of $f$ Hz, we can perform the translations into integral units as follows:

First, define our distance unit:
$$\delta = {j_{max} \over 6 f^3} \mathrm{mm}$$

Then we can simply compute the 3 maximums:

$$
\begin{aligned}
j^{~\prime} &= \frac{j}{\delta f^3} = 6 \\
a^\prime &= \frac{a}{\delta f^2} = \frac{6af}{j} \\
v^\prime &= \frac{v}{\delta f} = \frac{6vf^2}{j} \\
S^\prime &= \frac{S}{\delta} = \frac{6Sf^3}{j}
\end{aligned}
$$



In [32]:
f, delta = sympy.symbols('f,delta')
(a_max / (f**2 * delta)).subs(delta, j_max / 6 / f**3)

6⋅aₘₐₓ⋅f
────────
  jₘₐₓ  

## Polynomial evaluation

As our position equation is a polynomial, we can evaluate it quickly at successive positions using the method of finite differences.
A semi-naiive evaluation of the formula would take 6 multiplications and 4 additions, whereas FD results in only the four additions.

The differences can be calculated as follows:

In [23]:
eq1 = seg_d()['dp']
def fd(eqn, var=t):
    return (eqn.subs(var, var+1) - eqn).simplify()
    
fd1 = fd(eq1)
fd2 = fd(fd1)
fd3 = fd(fd2)

{sympy.Symbol(f"FD_{i}"): e.subs(t,0).simplify() for i, e in  enumerate([fd1, fd2, fd3])}

⎧     a₀   j                          ⎫
⎨FD₀: ── + ─ + v₀, FD₁: a₀ + j, FD₂: j⎬
⎩     2    6                          ⎭

## Resulting inaccuracy

Obviously, the step size and optimal segment times calculated above will not be integral. This means that some fudging is necessary to move the correct amount, and some more fudging might be necessary to actually reach the maximum velocity.

This can be done fairly easily by rounding each of the $t_*$ values caclulated using the above formulas down from their exact values. We then have exact values for the position at the end of each segment. By summing those, we can calculate how far the puck would move in each segment, and therefore the total distance moved.

Now we have only to increase each as appropriate. We can't increase $t_j$ because rounding $t_j$ up would result in accellerating faster than $a_{max}$.

$t_a$ is definitely underestimated, though, because it assumes that we've actually reached the full accelleration. $\delta v_3$ remains constant no matter the value of $t_a$, so we can simply calculate $$t_a^\prime  = t_a + {v_{max}-v_4 \over a_3}$$

This obviously increases $v_4$ to something closer to the target speed; we'll call the new value $v_4^\prime$. We then calculate $t_v$

In [61]:
p1s3["pe"]

         ⎛  2                   2⎞
jₘₐₓ⋅t_j⋅⎝tₐ  + 3⋅tₐ⋅t_j + 2⋅t_j ⎠
──────────────────────────────────
                2                 